In [ ]:
import os
import time
import jwt
import requests

admin_api_url = ""
admin_api_key = ""

def _create_jwt(admin_api_key):
    id_, secret = admin_api_key.split(':')
    iat = int(time.time())
    exp = iat + 5 * 60  # 5 minutes
    header = {'alg': 'HS256', 'kid': id_}
    payload = {
        'iat': iat,
        'exp': exp,
        'aud': '/v5/admin/'  # Adjust depending on your Ghost version
    }
    token = jwt.encode(payload, bytes.fromhex(secret), algorithm='HS256', headers=header)
    return token


In [ ]:
# Get token
jwt_token = _create_jwt(os.getenv("GHOST_ADMIN_API_KEY"))

headers = {
    'Authorization': f'Ghost {jwt_token}',
    'Content-Type': 'application/json'
}

deleted_post = True

while (deleted_post):
    # GET /admin/posts/
    response = requests.get(os.path.join(admin_api_url, "posts"), headers=headers)
    dict_response = response.json()

    if (len(dict_response.get("posts")) == 0):
        deleted_post = False
        break

    # Iterate posts
    for p in dict_response.get("posts"):
        # Post ID
        post_id = p.get("id")

        # DELETE /admin/posts/{id}/
        r = requests.delete(os.path.join(admin_api_url, "posts", "{}".format(post_id)), headers=headers)
        print("Post:", post_id, "Status:", r.status_code, r.text)